In [0]:
import threading
from datetime import datetime, timedelta

def run_spark():
    spark
    ist_time = datetime.utcnow() + timedelta(hours=5, minutes=30)
    print(f"Executed at: {ist_time}")
    threading.Timer(1140, run_spark).start()

run_spark()

Executed at: 2025-05-22 19:06:08.647534


In [0]:
storage_account = "mksoliststorageaccount"
application_id = "5e4dc1f8-f429-4eb6-8888-4f4abd15d59f"
directory_id = "15e203e9-bdac-4076-bc61-29fb7005e633"
service_credential = "<olistAppRegistration - Secrets and certificates - value>"

spark.conf.set(f"fs.azure.account.auth.type.{storage_account}.dfs.core.windows.net", "OAuth")
spark.conf.set(f"fs.azure.account.oauth.provider.type.{storage_account}.dfs.core.windows.net", 
               "org.apache.hadoop.fs.azurebfs.oauth2.ClientCredsTokenProvider")
spark.conf.set(f"fs.azure.account.oauth2.client.id.{storage_account}.dfs.core.windows.net", application_id)
spark.conf.set(f"fs.azure.account.oauth2.client.secret.{storage_account}.dfs.core.windows.net", service_credential)
spark.conf.set(f"fs.azure.account.oauth2.client.endpoint.{storage_account}.dfs.core.windows.net", 
               f"https://login.microsoftonline.com/{directory_id}/oauth2/token")

In [0]:
df = spark.read.format("csv").option("header", "true").load(f"abfss://olistdata@mksoliststorageaccount.dfs.core.windows.net/bronze/olist_customers_dataset.csv")
# display(df)

In [0]:
base_path = "abfss://olistdata@mksoliststorageaccount.dfs.core.windows.net/bronze/"
orders_path = base_path + "olist_orders_dataset.csv"
payments_path = base_path + "olist_order_payments_dataset.csv"
reviews_path = base_path + "olist_order_reviews_dataset.csv"
items_path = base_path + "olist_order_items_dataset.csv"
customers_path = base_path + "olist_customers_dataset.csv"
sellers_path = base_path + "olist_sellers_dataset.csv"
geolocation_path = base_path + "olist_geolocation_dataset.csv"
products_path = base_path + "olist_products_dataset.csv"

orders_df = spark.read.format("csv").option("header", "true").load(orders_path)
payments_df = spark.read.format("csv").option("header", "true").load(payments_path)
reviews_df = spark.read.format("csv").option("header", "true").load(reviews_path)
items_df = spark.read.format("csv").option("header", "true").load(items_path)
customers_df = spark.read.format("csv").option("header", "true").load(customers_path)
sellers_df = spark.read.format("csv").option("header", "true").load(sellers_path)
geolocation_df = spark.read.format("csv").option("header", "true").load(geolocation_path)
products_df = spark.read.format("csv").option("header", "true").load(products_path)


## Reading Data From Mongo DB

In [0]:
import pymongo
from pymongo import MongoClient

In [0]:
# importing module
from pymongo import MongoClient

hostname = "pjdir.h.filess.io"
database = "olistProjectNoSQL_sailpainus"
port = "27018"
username = "olistProjectNoSQL_sailpainus"
password = "9a884b18a31f961088eedffdc4063ba8370c160f"

uri = "mongodb://" + username + ":" + password + "@" + hostname + ":" + port + "/" + database

# Connect with the portnumber and host
client = MongoClient(uri)

# Access database
mydatabase = client[database]
mydatabase

Database(MongoClient(host=['pjdir.h.filess.io:27018'], document_class=dict, tz_aware=False, connect=True), 'olistProjectNoSQL_sailpainus')

In [0]:
import pandas as pd
collection = mydatabase['product_categories']
display(collection)
mongo_data = pd.DataFrame(collection.find())
# mongo_data

Collection(Database(MongoClient(host=['pjdir.h.filess.io:27018'], document_class=dict, tz_aware=False, connect=True), 'olistProjectNoSQL_sailpainus'), 'product_categories')

### Cleaning the Data

In [0]:
from pyspark.sql.functions import col,datediff,to_date,current_date,when


In [0]:
def clean_df(df):
    return df.dropDuplicates().na.drop("all")

initial_count = orders_df.count()
orders_df = clean_df(orders_df)
final_count = orders_df.count()

print(f"Initial count: {initial_count}, Final count: {final_count}")
# display(orders_df)

Initial count: 99441, Final count: 99441


In [0]:
# convert Date Colums

orders_df = orders_df.withColumn("order_purchase_timestamp", to_date(col("order_purchase_timestamp")))\
    .withColumn("order_delivered_customer_date", to_date(col("order_delivered_customer_date")))\
        .withColumn("order_estimated_delivery_date", to_date(col("order_estimated_delivery_date")))

In [0]:
# Calculate Delivery and Time Delays

orders_df = orders_df.withColumn("actual_delivery_time", datediff("order_delivered_customer_date", "order_purchase_timestamp"))
orders_df = orders_df.withColumn("estimated_delivery_time", datediff("order_estimated_delivery_date", "order_purchase_timestamp"))
orders_df =orders_df.withColumn("Delay Time", col("actual_delivery_time") - col("estimated_delivery_time"))

# display(orders_df)

In [0]:
# display(orders_df.tail(5))

## Joining

In [0]:
payments_df.columns,items_df.columns

(['order_id',
  'payment_sequential',
  'payment_type',
  'payment_installments',
  'payment_value'],
 ['order_id',
  'order_item_id',
  'product_id',
  'seller_id',
  'shipping_limit_date',
  'price',
  'freight_value'])

In [0]:
orders_cutomers_df = orders_df.join(customers_df, orders_df.customer_id == customers_df.customer_id,"left")

orders_payments_df = orders_cutomers_df.join(payments_df, orders_cutomers_df.order_id == payments_df.order_id,"left")

orders_items_df = orders_payments_df.join(items_df,"order_id","left")

orders_items_products_df = orders_items_df.join(products_df, orders_items_df.product_id == products_df.product_id,"left")

final_df = orders_items_products_df.join(sellers_df, orders_items_products_df.seller_id == sellers_df.seller_id,"left")

In [0]:
# display(final_df)

In [0]:
mongo_data.drop('_id',axis=1,inplace=True)

mongo_sparf_df = spark.createDataFrame(mongo_data)
# display(mongo_sparf_df)

In [0]:
final_df = final_df.join(mongo_sparf_df,"product_category_name","left")

In [0]:
# display(final_df)

In [0]:
def remove_duplicate_columns(df):
    columns = df.columns

    seen_columns = set()
    columns_to_drop = []

    for column in columns:
        if column in seen_columns:
            columns_to_drop.append(column)
        else:
            seen_columns.add(column)
    
    df_cleaned = df.drop(*columns_to_drop)
    return df_cleaned

final_df = remove_duplicate_columns(final_df)

In [0]:
final_df.write.mode("overwrite").parquet("abfss://olistdata@mksoliststorageaccount.dfs.core.windows.net/silver")

In [0]:
display(final_df)

product_category_name order_status order_purchase_timestamp order_approved_at order_delivered_carrier_date order_delivered_customer_date order_estimated_delivery_date actual_delivery_time estimated_delivery_time Delay Time customer_unique_id customer_zip_code_prefix customer_city customer_state payment_sequential payment_type payment_installments payment_value order_item_id shipping_limit_date price freight_value product_name_lenght product_description_lenght product_photos_qty product_weight_g product_length_cm product_height_cm product_width_cm seller_zip_code_prefix seller_city seller_state product_category_name_english instrumentos_musicais delivered 2018-03-07 2018-03-09 03:00:35 2018-03-14 02:08:26 2018-03-19 2018-03-29 12 22 -10 3ed766ba830792bcc9ad889d2607eab7 09811 sao bernardo do campo SP 1 boleto 1 78.1500015 1 2018-03-15 02:30:36 59.90 18.25 55 541 3 2750 103 12 17 86073 londrina PR musical_instruments beleza_saude delivered 2018-08-14 2018-08-14 18:23:55 2018-08-16 09:02:00 2018-08-21 2018-08-30 7 16 -9 6f90f04011f53535e2ed7add0e6e9775 14990 irapua SP 1 credit_card 2 30.7900009 1 2018-08-17 18:23:55 18.00 12.79 31 2737 1 150 16 5 11 06763 taboao da serra SP health_beauty cama_mesa_banho delivered 2017-09-13 2017-09-15 02:24:49 2017-09-20 13:35:16 2017-10-03 2017-10-16 20 33 -13 18bbfd7c77ff481bac5ae34fe5b8cc52 78780 alto araguaia MT 1 boleto 1 62.7400017 1 2017-09-26 02:24:49 45.95 16.79 47 161 2 350 25 8 19 14940 ibitinga SP bed_bath_table bebes delivered 2017-11-13 2017-11-13 16:56:00 2017-11-16 18:41:59 2017-11-24 2017-12-04 11 21 -10 6ac3687282ae6cf1976b4cc39677f95c 93010 sao leopoldo RS 1 credit_card 9 147.160004 1 2017-11-20 16:56:00 130.00 17.16 55 704 4 5650 60 20 50 81770 curitiba PR baby moveis_decoracao delivered 2018-03-21 2018-03-21 15:48:35 2018-03-22 20:02:51 2018-04-06 2018-04-10 16 20 -4 020311f9fc67a990f3d43b481398a259 81280 curitiba PR 1 credit_card 1 60.2200012 1 2018-03-27 15:48:35 44.99 15.23 34 786 5 550 18 35 18 03929 sao paulo SP furniture_decor cama_mesa_banho delivered 2018-01-17 2018-01-17 16:52:19 2018-01-25 15:39:01 2018-02-06 2018-02-19 20 33 -13 cc61ecdda15905388185bfd77969ae72 36213 dores de campos MG 1 credit_card 10 166.350006 1 2018-01-23 16:52:19 138.00 28.35 49 1077 1 4500 26 26 36 88359 brusque SC bed_bath_table esporte_lazer delivered 2017-09-14 2017-09-15 16:44:24 2017-09-18 16:13:17 2017-10-10 2017-10-18 26 34 -8 882a0803e178b947070fc52b14965102 66080 belem PA 1 credit_card 7 146.240005 1 2017-09-21 16:44:24 113.00 33.24 45 2950 1 1625 29 21 21 14070 ribeirao preto SP sports_leisure brinquedos delivered 2018-07-24 2018-07-24 22:10:19 2018-07-25 12:15:00 2018-07-26 2018-08-09 2 16 -14 f3832392e675c6ffa590ac21b517b47d 30644 belo horizonte MG 1 voucher 1 386.649994 1 2018-07-30 22:10:19 369.00 17.65 57 679 5 6750 55 15 16 36407 conselheiro lafaiete MG toys informatica_acessorios delivered 2018-03-20 2018-03-20 16:56:06 2018-03-26 20:32:08 2018-04-13 2018-04-06 24 17 7 1ee910b8be2fb6a731b54edf304e1b6f 05849 sao paulo SP 1 credit_card 1 202.259995 1 2018-03-26 16:56:06 185.00 17.26 56 156 1 750 36 11 20 20031 rio de janeiro RJ computers_accessories brinquedos delivered 2017-01-29 2017-01-29 22:33:34 2017-01-30 08:27:47 2017-02-08 2017-03-20 10 50 -40 903fccb1294b588a6c82921ca23acd0d 59086 natal RN 1 credit_card 4 157.990005 1 2017-02-02 22:14:49 129.99 28.00 59 1629 3 5250 51 15 52 89204 joinville SC toys beleza_saude delivered 2018-06-25 2018-06-25 11:57:45 2018-06-29 14:07:00 2018-07-11 2018-07-23 16 28 -12 dd14af9ed633811cf5a95244633422cc 45051 vitoria da conquista BA 1 credit_card 2 72.2699966 1 2018-06-29 11:57:45 49.99 22.28 53 532 1 200 16 14 12 13600 sao paulo SP health_beauty esporte_lazer delivered 2017-08-30 2017-08-30 20:30:09 2017-08-31 21:38:10 2017-09-20 2017-09-25 21 26 -5 07f73198f5bbc83c1ad9806a7ca28144 49095 aracaju SE 1 credit_card 5 71.3700027 1 2017-09-05 20:30:09 45.99 25.38 59 1013 3 200 20 7 12 88020 florianopolis SC sports_leisure moveis_decoracao deli

Databricks visualization. Run in Databricks to view.